<a href="https://colab.research.google.com/github/krakowiakpawel9/neural-network-course/blob/master/07_rnn/02_text_classifier.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
%tensorflow_version 2.x
import numpy as np
import os

from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Embedding, Flatten

TensorFlow 2.x selected.


In [0]:
# !wget https://storage.googleapis.com/esmartdata-courses-files/ann-course/reviews.zip

In [0]:
# !unzip -q reviews.zip

In [0]:
data_dir = './reviews'
train_dir = os.path.join(data_dir, 'train')

train_texts = []
train_labels = []

for label_type in ['neg', 'pos']:
    dir_name = os.path.join(train_dir, label_type)
    for fname in os.listdir(dir_name):
        if fname[-4:] == '.txt':
            f = open(os.path.join(dir_name, fname))
            train_texts.append(f.read())
            f.close()
            if label_type == 'neg':
                train_labels.append(0)
            else:
                train_labels.append(1)

In [0]:
test_dir = os.path.join(data_dir, 'test')

test_texts = []
test_labels = []

for label_type in ['neg', 'pos']:
    dir_name = os.path.join(test_dir, label_type)
    for fname in os.listdir(dir_name):
        if fname[-4:] == '.txt':
            f = open(os.path.join(dir_name, fname))
            test_texts.append(f.read())
            f.close()
            if label_type == 'neg':
                test_labels.append(0)
            else:
                test_labels.append(1)

In [0]:
train_texts[:10]

['Lauren Bacall and Charles Boyer do not provide the right chemistry here in this 1945 film.<br /><br />There is a good story here about the Axis trying to obtain coal to use for the upcoming war. Unfortunately, this part of the story is not emphasized. Instead, we deal with a supposedly bungling Boyer. By the way, Bacall is as British as Vladimir Putin.<br /><br />The real acting kudos goes to veteran Oscar winner Katina Paxinou. As was the case with her memorable Pilar in the 1943 Oscar winner, "For Whom the Bell Tolls," Paxinou again plays a Spanish revolutionary but this time she is a double-crossing counter-spy for the pro-Franco group. She is quite a vicious character here;especially, when she throws a 14 year old child out the window. She believed that Boyer had given the child important material to hide.',
 'May the saints preserve us, because this movie is not going to help.<br /><br />Someone with access needs to e-mail Mel Gibson and tell him we need a faithful production of

In [0]:
train_labels[:10]

[0, 0, 0, 0, 0, 0, 0, 0, 0, 0]

In [0]:
train_labels[-10:]

[1, 1, 1, 1, 1, 1, 1, 1, 1, 1]

In [0]:
maxlen = 100   # skracamy recenzje do 100 słów
num_words = 10000    # 10000 najczęściej pojawaijących się słów
embedding_dim = 100

tokenizer = Tokenizer(num_words=num_words)
tokenizer.fit_on_texts(train_texts)

In [0]:
list(tokenizer.index_word.items())[:20]

[(1, 'the'),
 (2, 'and'),
 (3, 'a'),
 (4, 'of'),
 (5, 'to'),
 (6, 'is'),
 (7, 'br'),
 (8, 'in'),
 (9, 'it'),
 (10, 'i'),
 (11, 'this'),
 (12, 'that'),
 (13, 'was'),
 (14, 'as'),
 (15, 'for'),
 (16, 'with'),
 (17, 'movie'),
 (18, 'but'),
 (19, 'film'),
 (20, 'on')]

In [0]:
sequences = tokenizer.texts_to_sequences(train_texts)
print(sequences[:3])

[[6192, 4844, 2, 1391, 6538, 78, 21, 1751, 1, 205, 1171, 130, 8, 11, 5674, 19, 7, 7, 47, 6, 3, 49, 62, 130, 41, 1, 266, 5, 5975, 8422, 5, 358, 15, 1, 7364, 322, 469, 11, 170, 4, 1, 62, 6, 21, 302, 72, 852, 16, 3, 1500, 6538, 31, 1, 93, 4844, 6, 14, 695, 14, 7, 7, 1, 144, 113, 3584, 268, 5, 2485, 731, 2278, 14, 13, 1, 417, 16, 38, 903, 8, 1, 7262, 731, 2278, 15, 931, 1, 4010, 171, 295, 3, 1866, 4174, 18, 11, 55, 56, 6, 3, 1402, 6041, 4801, 2537, 15, 1, 3331, 4716, 601, 56, 6, 176, 3, 3815, 106, 130, 258, 51, 56, 2876, 3, 2425, 288, 151, 503, 43, 1, 2043, 56, 2410, 12, 6538, 66, 345, 1, 503, 671, 815, 5, 2411], [200, 1, 8169, 175, 85, 11, 17, 6, 21, 167, 5, 335, 7, 7, 291, 16, 4558, 735, 5, 959, 4717, 3765, 8288, 2, 373, 87, 72, 356, 3, 2718, 362, 4, 6539, 139, 12, 162, 44, 139, 8, 1138, 16, 1, 1706, 4845, 12, 6, 1, 6887, 15, 29, 679, 1005, 4676, 7, 7, 1, 1132, 234, 3070, 2052, 4, 6539, 94, 72, 591, 104, 180, 83, 135, 6, 47, 35, 73, 599, 8, 1, 62, 330, 135, 23, 29, 131, 1053, 3975, 4, 22

In [0]:
word_index = tokenizer.word_index
print(f'{len(word_index)} unikatowych słów.')

88582 unikatowych słów.


In [0]:
train_data = pad_sequences(sequences, maxlen=maxlen)
train_data.shape

(25000, 100)

In [0]:
train_data[:3]

array([[  11,  170,    4,    1,   62,    6,   21,  302,   72,  852,   16,
           3, 1500, 6538,   31,    1,   93, 4844,    6,   14,  695,   14,
           7,    7,    1,  144,  113, 3584,  268,    5, 2485,  731, 2278,
          14,   13,    1,  417,   16,   38,  903,    8,    1, 7262,  731,
        2278,   15,  931,    1, 4010,  171,  295,    3, 1866, 4174,   18,
          11,   55,   56,    6,    3, 1402, 6041, 4801, 2537,   15,    1,
        3331, 4716,  601,   56,    6,  176,    3, 3815,  106,  130,  258,
          51,   56, 2876,    3, 2425,  288,  151,  503,   43,    1, 2043,
          56, 2410,   12, 6538,   66,  345,    1,  503,  671,  815,    5,
        2411],
       [  62,  330,  135,   23,   29,  131, 1053, 3975,    4, 2205,   20,
          11,  592,    7,    7,    1,   61,  279,   11,  185,    3,  104,
           6,   12,    1,  307,   16,    8,    9, 6539, 3070,   13,  430,
           2,  884,    1,  297,    7,    7,   48,    6,   57,  430,   46,
          81,   77,  10

In [0]:
train_labels = np.asarray(train_labels)
train_labels

array([0, 0, 0, ..., 1, 1, 1])

In [0]:
indices = np.arange(train_data.shape[0])
np.random.shuffle(indices)
train_data = train_data[indices]
train_labels = train_labels[indices]

train_data.shape

(25000, 100)

In [0]:
training_samples = 15000
validation_samples = 10000

X_train = train_data[:training_samples]
y_train = train_labels[:training_samples]
X_val = train_data[training_samples: training_samples + validation_samples]
y_val = train_labels[training_samples: training_samples + validation_samples]

In [0]:
# !wget http://nlp.stanford.edu/data/glove.6B.zip

In [0]:
# !unzip -q glove.6B.zip

In [0]:
model = Sequential()
model.add(Embedding(num_words, embedding_dim, input_length=maxlen))
model.add(Flatten())
model.add(Dense(32, activation='relu'))
model.add(Dense(1, activation='sigmoid'))
model.summary()

Model: "sequential_2"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_2 (Embedding)      (None, 100, 100)          1000000   
_________________________________________________________________
flatten_2 (Flatten)          (None, 10000)             0         
_________________________________________________________________
dense_4 (Dense)              (None, 32)                320032    
_________________________________________________________________
dense_5 (Dense)              (None, 1)                 33        
Total params: 1,320,065
Trainable params: 1,320,065
Non-trainable params: 0
_________________________________________________________________


In [0]:
model.compile(optimizer='rmsprop',
              loss='binary_crossentropy',
              metrics=['accuracy'])

In [0]:
history = model.fit(X_train, y_train, batch_size=32, epochs=5, validation_data=(X_val, y_val))

Train on 15000 samples, validate on 10000 samples
Epoch 1/5
15000/15000 [==============================] - 9s 567us/sample - loss: 0.4604 - accuracy: 0.7725 - val_loss: 0.3669 - val_accuracy: 0.8323
Epoch 2/5
15000/15000 [==============================] - 8s 532us/sample - loss: 0.1474 - accuracy: 0.9461 - val_loss: 0.4250 - val_accuracy: 0.8261
Epoch 3/5
15000/15000 [==============================] - 8s 541us/sample - loss: 0.0161 - accuracy: 0.9956 - val_loss: 0.6069 - val_accuracy: 0.8180
Epoch 4/5
15000/15000 [==============================] - 8s 528us/sample - loss: 6.7630e-04 - accuracy: 0.9998 - val_loss: 0.7881 - val_accuracy: 0.8278
Epoch 5/5
15000/15000 [==============================] - 8s 529us/sample - loss: 1.9881e-05 - accuracy: 1.0000 - val_loss: 1.0008 - val_accuracy: 0.8216


In [0]:
def plot_hist(history):
    import pandas as pd
    import plotly.graph_objects as go
    hist = pd.DataFrame(history.history)
    hist['epoch'] = history.epoch

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=hist['epoch'], y=hist['accuracy'], name='accuracy', mode='markers+lines'))
    fig.add_trace(go.Scatter(x=hist['epoch'], y=hist['val_accuracy'], name='val_accuracy', mode='markers+lines'))
    fig.update_layout(width=1000, height=500, title='accuracy vs. val accuracy', xaxis_title='Epoki', yaxis_title='accuracy', yaxis_type='log')
    fig.show()

    fig = go.Figure()
    fig.add_trace(go.Scatter(x=hist['epoch'], y=hist['loss'], name='loss', mode='markers+lines'))
    fig.add_trace(go.Scatter(x=hist['epoch'], y=hist['val_loss'], name='val_loss', mode='markers+lines'))
    fig.update_layout(width=1000, height=500, title='loss vs. val loss', xaxis_title='Epoki', yaxis_title='loss', yaxis_type='log')
    fig.show()

plot_hist(history)

In [0]:
sequences = tokenizer.texts_to_sequences(test_texts)
X_test = pad_sequences(sequences, maxlen=maxlen)
y_test = np.asarray(test_labels)

model.evaluate(X_test, y_test, verbose=0)

[1.0165424507331848, 0.81668]

### GloVe

In [0]:
embeddings_index = {}
with open('glove.6B.100d.txt') as file:
    for line in file:
        values = line.split()
        word = values[0]
        coefs = np.asarray(values[1:], dtype='float32')
        embeddings_index[word] = coefs

print(f'Znaleziono {len(embeddings_index)} słów.')

Znaleziono 400000 słów.


In [0]:
embeddings_index.keys()

dict_keys(['the', ',', '.', 'of', 'to', 'and', 'in', 'a', '"', "'s", 'for', '-', 'that', 'on', 'is', 'was', 'said', 'with', 'he', 'as', 'it', 'by', 'at', '(', ')', 'from', 'his', "''", '``', 'an', 'be', 'has', 'are', 'have', 'but', 'were', 'not', 'this', 'who', 'they', 'had', 'i', 'which', 'will', 'their', ':', 'or', 'its', 'one', 'after', 'new', 'been', 'also', 'we', 'would', 'two', 'more', "'", 'first', 'about', 'up', 'when', 'year', 'there', 'all', '--', 'out', 'she', 'other', 'people', "n't", 'her', 'percent', 'than', 'over', 'into', 'last', 'some', 'government', 'time', '$', 'you', 'years', 'if', 'no', 'world', 'can', 'three', 'do', ';', 'president', 'only', 'state', 'million', 'could', 'us', 'most', '_', 'against', 'u.s.', 'so', 'them', 'what', 'him', 'united', 'during', 'before', 'may', 'since', 'many', 'while', 'where', 'states', 'because', 'now', 'city', 'made', 'like', 'between', 'did', 'just', 'national', 'day', 'country', 'under', 'such', 'second', 'then', 'company', 'group

In [0]:
embeddings_index['movie']

array([ 0.38251  ,  0.14821  ,  0.60601  , -0.51533  ,  0.43992  ,
        0.061053 , -0.62716  , -0.025385 ,  0.1643   , -0.22101  ,
        0.14423  , -0.37213  , -0.21683  , -0.08895  ,  0.097904 ,
        0.6561   ,  0.64455  ,  0.47698  ,  0.83849  ,  1.6486   ,
        0.88922  , -0.1181   , -0.012465 , -0.52082  ,  0.77854  ,
        0.48723  , -0.014991 , -0.14127  , -0.34747  , -0.29595  ,
        0.1028   ,  0.57191  , -0.045594 ,  0.026443 ,  0.53816  ,
        0.32257  ,  0.40788  , -0.043599 , -0.146    , -0.48346  ,
        0.32036  ,  0.55086  , -0.76259  ,  0.43269  ,  0.61753  ,
       -0.36503  , -0.60599  , -0.79615  ,  0.3929   , -0.23668  ,
       -0.34719  , -0.61201  ,  0.54747  ,  0.94812  ,  0.20941  ,
       -2.7771   , -0.6022   ,  0.8495   ,  1.2549   ,  0.017893 ,
       -0.041901 ,  2.1147   , -0.026618 , -0.28104  ,  0.68124  ,
       -0.14165  ,  0.99249  ,  0.49879  , -0.67538  ,  0.6417   ,
        0.42303  , -0.27913  ,  0.063403 ,  0.68909  , -0.3618

In [0]:
embedding_matrix = np.zeros((num_words, embedding_dim))
for word, idx in word_index.items():
    embedding_vector = embeddings_index.get(word)
    if idx < num_words:
        if embedding_vector is not None:
            embedding_matrix[idx] = embedding_vector

In [0]:
embedding_matrix[:3]

array([[ 0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
         0.        ,  0.        ,  0.        ,  0. 

In [0]:
model = Sequential()
model.add(Embedding(num_words, embedding_dim, input_length=maxlen))
model.add(Flatten())
model.add(Dense(32, activation='relu'))
model.add(Dense(1, activation='sigmoid'))
model.summary()

Model: "sequential_3"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_3 (Embedding)      (None, 100, 100)          1000000   
_________________________________________________________________
flatten_3 (Flatten)          (None, 10000)             0         
_________________________________________________________________
dense_6 (Dense)              (None, 32)                320032    
_________________________________________________________________
dense_7 (Dense)              (None, 1)                 33        
Total params: 1,320,065
Trainable params: 1,320,065
Non-trainable params: 0
_________________________________________________________________


In [0]:
model.layers[0].set_weights([embedding_matrix])
model.layers[0].trainable = False

In [0]:
model.compile(optimizer='rmsprop',
              loss='binary_crossentropy',
              metrics=['accuracy'])

In [0]:
history = model.fit(X_train, y_train, batch_size=32, epochs=20, validation_data=(X_val, y_val))

Train on 15000 samples, validate on 10000 samples
Epoch 1/20
15000/15000 [==============================] - 5s 344us/sample - loss: 0.6613 - accuracy: 0.6328 - val_loss: 0.6630 - val_accuracy: 0.6144
Epoch 2/20
15000/15000 [==============================] - 4s 290us/sample - loss: 0.5290 - accuracy: 0.7396 - val_loss: 0.5992 - val_accuracy: 0.6872
Epoch 3/20
15000/15000 [==============================] - 4s 299us/sample - loss: 0.4772 - accuracy: 0.7766 - val_loss: 0.5680 - val_accuracy: 0.7112
Epoch 4/20
15000/15000 [==============================] - 4s 290us/sample - loss: 0.4194 - accuracy: 0.8105 - val_loss: 0.5745 - val_accuracy: 0.7109
Epoch 5/20
15000/15000 [==============================] - 4s 294us/sample - loss: 0.3818 - accuracy: 0.8287 - val_loss: 0.6111 - val_accuracy: 0.7101
Epoch 6/20
15000/15000 [==============================] - 4s 292us/sample - loss: 0.3497 - accuracy: 0.8461 - val_loss: 0.7009 - val_accuracy: 0.7011
Epoch 7/20
15000/15000 [==========================

In [0]:
plot_hist(history)    

In [0]:
model.evaluate(X_test, y_test, verbose=0)

[1.812715238456726, 0.68972]

### Simple RNN

In [0]:
from tensorflow.keras.layers import SimpleRNN, LSTM


In [0]:
model = Sequential()
model.add(Embedding(10000, 32))
model.add(SimpleRNN(32))
model.add(Dense(1, activation='sigmoid'))
model.summary()

Model: "sequential_8"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_8 (Embedding)      (None, None, 32)          320000    
_________________________________________________________________
simple_rnn_4 (SimpleRNN)     (None, 32)                2080      
_________________________________________________________________
dense_8 (Dense)              (None, 1)                 33        
Total params: 322,113
Trainable params: 322,113
Non-trainable params: 0
_________________________________________________________________


In [0]:
model.compile(optimizer='rmsprop',
              loss='binary_crossentropy',
              metrics=['accuracy'])

In [0]:
history = model.fit(X_train, y_train, batch_size=32, epochs=10, validation_data=(X_val, y_val))

Train on 15000 samples, validate on 10000 samples
Epoch 1/20
15000/15000 [==============================] - 16s 1ms/sample - loss: 0.5198 - accuracy: 0.7371 - val_loss: 0.4389 - val_accuracy: 0.8089
Epoch 2/20
15000/15000 [==============================] - 15s 997us/sample - loss: 0.3349 - accuracy: 0.8631 - val_loss: 0.3912 - val_accuracy: 0.8257
Epoch 3/20
15000/15000 [==============================] - 15s 992us/sample - loss: 0.2610 - accuracy: 0.8972 - val_loss: 0.3732 - val_accuracy: 0.8502
Epoch 4/20
15000/15000 [==============================] - 15s 991us/sample - loss: 0.2020 - accuracy: 0.9239 - val_loss: 0.3974 - val_accuracy: 0.8364
Epoch 5/20
15000/15000 [==============================] - 15s 993us/sample - loss: 0.1351 - accuracy: 0.9507 - val_loss: 0.4499 - val_accuracy: 0.8274
Epoch 6/20
15000/15000 [==============================] - 15s 997us/sample - loss: 0.0826 - accuracy: 0.9724 - val_loss: 0.5549 - val_accuracy: 0.8221
Epoch 7/20
15000/15000 [======================

In [0]:
plot_hist(history)

In [0]:
model = Sequential()
model.add(Embedding(10000, 32))
model.add(LSTM(32))
model.add(Dense(1, activation='sigmoid'))
model.summary()

Model: "sequential_9"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding_9 (Embedding)      (None, None, 32)          320000    
_________________________________________________________________
lstm (LSTM)                  (None, 32)                8320      
_________________________________________________________________
dense_9 (Dense)              (None, 1)                 33        
Total params: 328,353
Trainable params: 328,353
Non-trainable params: 0
_________________________________________________________________


In [0]:
model.compile(optimizer='rmsprop',
              loss='binary_crossentropy',
              metrics=['accuracy'])

In [0]:
history = model.fit(X_train, y_train, batch_size=32, epochs=10, validation_data=(X_val, y_val))

Train on 15000 samples, validate on 10000 samples
Epoch 1/10
15000/15000 [==============================] - 28s 2ms/sample - loss: 0.4649 - accuracy: 0.7771 - val_loss: 0.4190 - val_accuracy: 0.8078
Epoch 2/10
15000/15000 [==============================] - 25s 2ms/sample - loss: 0.2943 - accuracy: 0.8805 - val_loss: 0.3426 - val_accuracy: 0.8540
Epoch 3/10
15000/15000 [==============================] - 25s 2ms/sample - loss: 0.2480 - accuracy: 0.9061 - val_loss: 0.3663 - val_accuracy: 0.8557
Epoch 4/10
15000/15000 [==============================] - 25s 2ms/sample - loss: 0.2207 - accuracy: 0.9159 - val_loss: 0.3385 - val_accuracy: 0.8592
Epoch 5/10
15000/15000 [==============================] - 26s 2ms/sample - loss: 0.2025 - accuracy: 0.9215 - val_loss: 0.3563 - val_accuracy: 0.8463
Epoch 6/10
15000/15000 [==============================] - 25s 2ms/sample - loss: 0.1862 - accuracy: 0.9295 - val_loss: 0.3608 - val_accuracy: 0.8573
Epoch 7/10
15000/15000 [==============================] 